<a href="https://colab.research.google.com/github/aarongerston/CovidStats/blob/master/CovidStats.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
"""

"""

'\nINTRODUCTORY TEXT\n'

The Covid-19 pandemic is a goldmine for data exploration and data science because there were (and still are) so many factors that may guide the best course of action throughout the pandemic and future pandemics.

Here I lay out some very simple groundwork for basic data exploration using two simple data sources:
1. Covid-19 case

In [3]:
# This is a simple project.
# We will need numpy and pandas for basic data manipulation, and plotly for visualizations.

import numpy as np
import pandas as pd
import plotly.express as px

# Suppress annoying warnings
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
pd.options.mode.chained_assignment = None  # Suppress pandas SettingWithCopyWarning

# **1. Data acquisition**

In [69]:
# Read data

# 1. Covid-19 cases and deaths, daily, from Center for Systems Science and Engineering (CSSE) at Johns Hopkins University:
#	 https://www.kaggle.com/sudalairajkumar/novel-corona-virus-2019-dataset/data?select=covid_19_data.csv
df = pd.read_csv(r"../content/data/covid_19_data.csv")

# 2. Countries' populations (in 2019), from World Bank:
#	 https://data.worldbank.org/indicator/SP.POP.TOTL
pops = pd.read_csv(r"../content/data/world population.csv", header=2)

# Note: we're making a simplifying assumption here that population remains unchanged over time.
# A more accurate adjustment to this project would consider the change in population projections over the course of the pandemic.

Let's see what we've got:

In [70]:
df.head()

SNo ObservationDate Province/State  Country/Region      Last Update  \
0    1      01/22/2020          Anhui  Mainland China  1/22/2020 17:00   
1    2      01/22/2020        Beijing  Mainland China  1/22/2020 17:00   
2    3      01/22/2020      Chongqing  Mainland China  1/22/2020 17:00   
3    4      01/22/2020         Fujian  Mainland China  1/22/2020 17:00   
4    5      01/22/2020          Gansu  Mainland China  1/22/2020 17:00   

   Confirmed  Deaths  Recovered  
0        1.0     0.0        0.0  
1       14.0     0.0        0.0  
2        6.0     0.0        0.0  
3        1.0     0.0        0.0  
4        0.0     0.0        0.0

In [71]:
pops.head()

Country Name Country Code     Indicator Name Indicator Code       1960  \
0        Aruba          ABW  Population, total    SP.POP.TOTL    54211.0   
1  Afghanistan          AFG  Population, total    SP.POP.TOTL  8996973.0   
2       Angola          AGO  Population, total    SP.POP.TOTL  5454933.0   
3      Albania          ALB  Population, total    SP.POP.TOTL  1608800.0   
4      Andorra          AND  Population, total    SP.POP.TOTL    13411.0   

        1961       1962       1963       1964       1965  ...        2011  \
0    55438.0    56225.0    56695.0    57032.0    57360.0  ...    102046.0   
1  9169410.0  9351441.0  9543205.0  9744781.0  9956320.0  ...  30117413.0   
2  5531472.0  5608539.0  5679458.0  5735044.0  5770570.0  ...  24220661.0   
3  1659800.0  1711319.0  1762621.0  1814135.0  1864791.0  ...   2905195.0   
4    14375.0    15370.0    16412.0    17469.0    18549.0  ...     83747.0   

         2012        2013        2014        2015        2016        2017  \
0    102560.0    103159.0    103774.0    104341.0    104872.0    105366.0   
1  31161376.0  32269589.0  33370794.0  34413603.0  35383128.0  36296400.0   
2  25107931.0  26015780.0  26941779.0  27884381.0  28842484.0  29816748.0   
3   2900401.0   2895092.0   2889104.0   2880703.0   2876101.0   2873457.0   
4     82427.0     80774.0     79213.0     78011.0     77297.0     77001.0   

         2018        2019  Unnamed: 64  
0    105845.0    106314.0          NaN  
1  37172386.0  38041754.0          NaN  
2  30809762.0  31825295.0          NaN  
3   2866376.0   2854191.0          NaN  
4     77006.0     77142.0          NaN  

[5 rows x 65 columns]

As we can see, we have a few columns in each data set that are not relevant and some columns that need refinement for ease-of-use.

That sets us up for Step 2:
# **2. Preprocessing**

In [72]:
# Make some minor DataFrame adjustments for ease-of-use:

# Rename columns
df = df.rename(columns={'Country/Region': 'Country', 'ObservationDate': 'Date'})
pops = pops.rename(columns={'Country Name': 'Country', '2019': 'Population'})

# Select columns
pops = pops[['Country', 'Population']]
df = df[['Country', 'Date', 'Province/State', 'Confirmed', 'Deaths', 'Recovered']]

# Combine separated regions into singular entities for each country, by summing values grouped by country and date:
df = df.groupby(['Date', 'Country']).sum().reset_index()

# Print part of df as sanity check
df[df['Country'] == 'Mainland China'].sort_values(by='Date')

Date         Country  Confirmed  Deaths  Recovered
3      01/22/2020  Mainland China      547.0    17.0       28.0
14     01/23/2020  Mainland China      639.0    18.0       30.0
28     01/24/2020  Mainland China      916.0    26.0       36.0
40     01/25/2020  Mainland China     1399.0    42.0       39.0
55     01/26/2020  Mainland China     2062.0    56.0       49.0
...           ...             ...        ...     ...        ...
15757  05/25/2020  Mainland China    82992.0  4634.0    78277.0
15947  05/26/2020  Mainland China    82993.0  4634.0    78280.0
16137  05/27/2020  Mainland China    82995.0  4634.0    78288.0
16327  05/28/2020  Mainland China    82995.0  4634.0    78291.0
16515  05/29/2020  Mainland China     2163.0    21.0     2139.0

[129 rows x 5 columns]

One thing I noticed from the above printout is that the number of reported cases suddenly drops on the last date in the data set!

Let's investigate...

In [73]:
# Create dict mapping each country to any dates that experience a nonsensical decrease in total # of confirmed cases:
potentially_problematic = {country: df[df['Country']==country].sort_values(by="Date")[["Confirmed", "Deaths", "Recovered"]].diff(axis=0).sum(axis=1) for country in df["Country"].unique()}
problematic = {country: df[df['Country']==country].sort_values(by="Date").iloc[np.where(potentially_problematic[country].values < 0)]["Date"] for country in potentially_problematic.keys()}

# Count how many countries experience a nonsensical decrease in total confirmed cases from one date to the next, for each date in the data set:
problematic_dates = []
for dates in problematic.values():
  if len(dates):
    problematic_dates.extend(dates.tolist())
{date: problematic_dates.count(date) for date in np.unique(problematic_dates)}

{'01/23/2020': 1,
 '02/07/2020': 1,
 '02/21/2020': 1,
 '03/09/2020': 1,
 '03/10/2020': 2,
 '03/11/2020': 1,
 '03/13/2020': 1,
 '03/15/2020': 1,
 '03/16/2020': 3,
 '03/17/2020': 4,
 '03/18/2020': 3,
 '03/19/2020': 2,
 '03/22/2020': 1,
 '03/24/2020': 2,
 '03/26/2020': 1,
 '04/01/2020': 1,
 '04/14/2020': 1,
 '04/22/2020': 1,
 '04/24/2020': 1,
 '04/25/2020': 1,
 '04/26/2020': 1,
 '04/28/2020': 4,
 '04/29/2020': 1,
 '04/30/2020': 2,
 '05/01/2020': 1,
 '05/02/2020': 3,
 '05/07/2020': 2,
 '05/08/2020': 1,
 '05/10/2020': 1,
 '05/11/2020': 2,
 '05/12/2020': 1,
 '05/14/2020': 1,
 '05/19/2020': 1,
 '05/20/2020': 3,
 '05/21/2020': 1,
 '05/25/2020': 1,
 '05/28/2020': 1,
 '05/29/2020': 15}

Problems indeed. Looks like we have a few one-offs that we can chaulk up to human error, but the last date in the data set is clearly problematic. Easy fix: drop the last date from the whole data set.

In [74]:
# Remove problematic date from data
df = df[df["Date"] != '05/29/2020']

In [75]:
# Make sure the lists contain the same countries (and refer to them the same way):

df_countries = set(df["Country"])
print("# `df` countries:")
print(len(df_countries))

pops_countries = set(pops["Country"])
print("\n# `pops` countries:")
print(len(pops_countries))

print("\nCountries listed in `pops` but not in `df`:")
print('\n'.join(list(pops_countries - df_countries)))
print("\nCountries listed in `df` but not in `pops`:")
print('\n'.join(list(df_countries - pops_countries)))

# `df` countries:
223

# `pops` countries:
264

Countries listed in `pops` but not in `df`:
Middle income
St. Martin (French part)
St. Lucia
Kiribati
Myanmar
Iran, Islamic Rep.
IDA total
Tuvalu
Samoa
Europe & Central Asia (excluding high income)
American Samoa
High income
Late-demographic dividend
Northern Mariana Islands
Congo, Dem. Rep.
South Asia (IDA & IBRD)
British Virgin Islands
Caribbean small states
Yemen, Rep.
St. Vincent and the Grenadines
Europe & Central Asia (IDA & IBRD countries)
Turkmenistan
Egypt, Arab Rep.
Central Europe and the Baltics
Korea, Rep.
East Asia & Pacific (IDA & IBRD countries)
Korea, Dem. People’s Rep.
China
IBRD only
Macao SAR, China
Other small states
Europe & Central Asia
Micronesia, Fed. Sts.
Low & middle income
East Asia & Pacific
Nauru
Russian Federation
IDA only
New Caledonia
Post-demographic dividend
St. Kitts and Nevis
Middle East & North Africa (excluding high income)
Hong Kong SAR, China
Slovak Republic
Marshall Islands
Lao PDR
Latin America & 

Looks like we've got some database alignment to do for the handful of countries that are listed in both data sets but under different names:

In [76]:
pops = pops.replace({'Brunei Darussalam': 'Brunei',
                     'Congo, Dem. Rep.': 'Congo (Kinshasa)',
                     'Egypt, Arab Rep.': 'Egypt',
                     'Hong Kong SAR, China': 'Hong Kong',
                     'Iran, Islamic Rep.': 'Iran',
                     "Cote d'Ivoire": 'Ivory Coast',
                     'Kyrgyz Republic': 'Kyrgyzstan',
                     'Lao PDR': 'Laos',
                     'Macao SAR, China': 'Macau',
                     'China': 'Mainland China',
                     'Myanmar': 'Burma',
                     'Congo, Rep.': 'Republic of the Congo',
                     'Russian Federation': 'Russia',
                     'St. Kitts and Nevis': 'Saint Kitts and Nevis',
                     'St. Lucia': 'Saint Lucia',
                     'St. Vincent and the Grenadines': 'Saint Vincent and the Grenadines',
                     'Slovak Republic': 'Slovakia',
                     'Korea, Rep.': 'South Korea',
                     'Syrian Arab Republic': 'Syria',
                     'Caribbean small states': 'The Bahamas',
                     'United Kingdom': 'UK',
                     'United States': 'US',
                     'Venezuela, RB': 'Venezuela',
                     'Yemen, Rep.': 'Yemen'})

In [77]:
# We can ignore countries listed in only one data set. They're not useful for us.

countries = set(df["Country"]) & set(pops["Country"])  # intersection
df = df[df["Country"].isin(countries)]  # Keep only rows with countries in both lists
pops = pops[pops["Country"].isin(countries)]

In [78]:
# Merge into a single DataFrame for convenience:
df = df.merge(pops, on="Country")

Date    Country  Confirmed  Deaths  Recovered  Population
0      01/22/2020  Hong Kong        0.0     0.0        0.0   7507400.0
1      01/23/2020  Hong Kong        2.0     0.0        0.0   7507400.0
2      01/24/2020  Hong Kong        2.0     0.0        0.0   7507400.0
3      01/25/2020  Hong Kong        5.0     0.0        0.0   7507400.0
4      01/26/2020  Hong Kong        8.0     0.0        0.0   7507400.0
...           ...        ...        ...     ...        ...         ...
15654  05/24/2020    Lesotho        2.0     0.0        0.0   2125268.0
15655  05/25/2020    Lesotho        2.0     0.0        0.0   2125268.0
15656  05/26/2020    Lesotho        2.0     0.0        0.0   2125268.0
15657  05/27/2020    Lesotho        2.0     0.0        0.0   2125268.0
15658  05/28/2020    Lesotho        2.0     0.0        1.0   2125268.0

[15659 rows x 6 columns]

In [88]:
# Finally, remove any columns with no population or country information:
df = df[~df["Country"].isna()]
df = df[~(df["Population"].isna() | df["Population"] == 0)]

# **3. Data Exploration**
(and further preprocessing)

For starters, let's get an understanding of our data distribution to see if we have any outliers or wonky behavior:

In [91]:
# Group data by country and sort by date
# df = df[df['Confirmed'] > 0]
df = df.groupby(['Date', 'Country']).sum().reset_index()

In [92]:
# Let's just take a snapshot of the data at the last date available in this data set to get an idea.

# Plot covid case distributions:
most_recent_cases = df[df["Date"] == df["Date"].iloc[-1]]
most_recent_cases.sort_values(by="Confirmed", inplace=True)
most_recent_cases["log cases"] = np.log(most_recent_cases["Confirmed"])
fig = px.bar(most_recent_cases,
             x='Country',
             y='log cases',
             color='log cases',
             hover_data='Confirmed',
             title=f'Log distribution of confirmed Covid cases on {df["Date"].iloc[-1]}')
fig.update_layout(xaxis_tickfont_size=8,
                  xaxis_tickangle=-45,
                  title_x=0.5)

Luckily, though it is clear that values vary widely, it looks like we have a very workable distribution that doesn't seem to need any outlier handling.

In [139]:
# Calculate and create columns:

# 1. 'Case Rate': % of population with confirmed cases
df['Case Rate'] = df['Confirmed'] / df['Population'] * 100

# 2. 'Fatalities / million': # of deaths per million people
df['Fatalities / million'] = df['Deaths'] / df['Population'] * 1e6

# 3. 'Mortality Rate': % of confirmed cases that ended in fatality
df['Mortality Rate'] = df['Deaths'] / df['Confirmed'] * 100

# 4. 'Fatalities / million': number of fatalities normalized by population
df['Mortality Rate / million'] = df['Mortality Rate'] / df['Population'] * 1e6

# 5. 'Recovery Rate': % of confirmed cases ending in recovery
df['Recovery Rate'] = df['Recovered'] / df['Confirmed']

# **4. Visualize**

In [140]:
choro1 = px.choropleth(df,
                       locations='Country',
                       locationmode='country names',
                       color='Confirmed',
                       labels={'Confirmed': 'Confirmed Cases'},
                       hover_name='Country',
                       hover_data=["Confirmed", "Population"],
                       animation_frame='Date',
                       range_color=[0, 5e5])
choro1.update_layout(title_text='Confirmed Covid-19 Cases',
                     title_x=0.5,
                     geo=dict(showframe=False, showcoastlines=False))
choro1.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 50
choro1.show()

If the pandemic spread were not regulated differently from country to country, we would intuitively expect to see rising numbers of cases spreading around the point of origin (China) and big transport hubs (like the US). It follows too that countries with larger populations, particularly with dense population centers, are likely to eventually experience greater exposure.

To some extent, that explains some of what we see above, along with China's timely effort to contain the disease spread and the US's failure to do the same.

What would be more interesting is to see to what extent different countries managed to contain disease spread and severity. To start, let's map the rate of disease spread, i.e. number of cases normalized by population:

In [141]:
choro2 = px.choropleth(df,
                       locations='Country',
                       locationmode='country names',
                       color='Case Rate',
                       labels={'Case Rate': 'Case Rate (%)'},
                       hover_name='Country',
                       animation_frame='Date',
                       range_color=[0, 0.501])
choro2.update_layout(title_text='Confirmed Covid-19 Case Rate',
                     annotations=[dict(x=0.53, y=1.05, showarrow=False,
                                       text='(% of population with confirmed cases)')],
                     title_x=0.5,
                     geo=dict(showframe=False, showcoastlines=False))
choro2.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 50
choro2.show()

df.groupby(by="Country").agg({"Case Rate": "max"}).sort_values(by="Case Rate", ascending=False).head(n=15)

Case Rate
Country              
San Marino   1.978736
Qatar        1.797768
Andorra      0.989085
Luxembourg   0.646560
Bahrain      0.612489
Singapore    0.582951
Kuwait       0.573129
US           0.524542
Spain        0.505357
Belgium      0.503733
Ireland      0.502707
Iceland      0.499567
Chile        0.458753
Peru         0.436103
Belarus      0.421027

Looks like a handful of countries really struggled to contain the virus, especially in the Middle East, Europe, and the Americas.

Unsurprisingly, countries with less frequent international travel experienced fewer cases, even when normalized by population.

Next let's see how well countries managed disease progression in confirmed cases:

In [142]:
choro3 = px.choropleth(df,
                       locations='Country',
                       locationmode='country names',
                       color='Mortality Rate',
                       labels={'Mortality Rate': 'Mortality Rate (%)'},
                       hover_name='Country',
                       hover_data=['Deaths'],
                       animation_frame='Date',
                       range_color=[0, 10])
choro3.update_layout(title_text='Covid-19 Mortality Rate',
                     annotations=[dict(x=0.54, y=1.05, showarrow=False,
                                       text='(% of confirmed cases resulting in fatality)')],
                     title_x=0.5,
                     geo=dict(showframe=False, showcoastlines=False))
choro3.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 50
choro3.show()

df.groupby(by="Country").tail(1).sort_values(by="Mortality Rate", ascending=False).head(n=20)

Date              Country  Confirmed   Deaths  Recovered  \
15587  05/28/2020                Yemen      278.0     57.0       11.0   
15424  05/28/2020              Belgium    57849.0   9388.0    15572.0   
15465  05/28/2020               France   186364.0  28665.0    67309.0   
15487  05/28/2020                Italy   231732.0  33142.0   150604.0   
15577  05/28/2020                   UK   270508.0  37919.0     1167.0   
15479  05/28/2020              Hungary     3816.0    509.0     1996.0   
15525  05/28/2020          Netherlands    46152.0   5922.0      178.0   
15414  05/28/2020  Antigua and Barbuda       25.0      3.0       19.0   
15566  05/28/2020               Sweden    35727.0   4266.0     4971.0   
15562  05/28/2020                Spain   237906.0  27119.0   150376.0   
15425  05/28/2020               Belize       18.0      2.0       16.0   
15516  05/28/2020               Mexico    81400.0   9044.0    56041.0   
15501  05/28/2020              Liberia      269.0     27.0      144.0   
15442  05/28/2020                 Chad      726.0     65.0      413.0   
15456  05/28/2020              Ecuador    38471.0   3313.0    18425.0   
15565  05/28/2020             Suriname       12.0      1.0        9.0   
15440  05/28/2020               Canada    89976.0   6982.0    46961.0   
15422  05/28/2020             Barbados       92.0      7.0       76.0   
15475  05/28/2020               Guyana      150.0     11.0       67.0   
15557  05/28/2020             Slovenia     1473.0    108.0     1356.0   

        Population  Case Rate  Fatalities / million  Mortality Rate  \
15587   29161922.0   0.000953              1.954604       20.503597   
15424   11484055.0   0.503733            817.481282       16.228457   
15465   67059887.0   0.277907            427.453747       15.381190   
15487   60297396.0   0.384315            549.642310       14.301866   
15577   66834405.0   0.404744            567.357486       14.017700   
15479    9769949.0   0.039059             52.098532       13.338574   
15525   17332850.0   0.266269            341.663373       12.831513   
15414      97118.0   0.025742             30.890257       12.000000   
15566   10285453.0   0.347355            414.760536       11.940549   
15562   47076781.0   0.505357            576.058928       11.399040   
15425     390353.0   0.004611              5.123568       11.111111   
15516  127575529.0   0.063805             70.891338       11.110565   
15501    4937374.0   0.005448              5.468494       10.037175   
15442   15946876.0   0.004553              4.076033        8.953168   
15456   17373662.0   0.221433            190.690944        8.611682   
15565     581372.0   0.002064              1.720069        8.333333   
15440   37589262.0   0.239366            185.744535        7.759847   
15422     287025.0   0.032053             24.388120        7.608696   
15475     782766.0   0.019163             14.052731        7.333333   
15557    2087946.0   0.070548             51.725476        7.331976   

       Mortality Rate / million  Recovery Rate  
15587                  0.703095       0.039568  
15424                  1.413129       0.269184  
15465                  0.229365       0.361170  
15487                  0.237189       0.649906  
15577                  0.209738       0.004314  
15479                  1.365266       0.523061  
15525                  0.740300       0.003857  
15414                123.561029       0.760000  
15566                  1.160916       0.139138  
15562                  0.242137       0.632082  
15425                 28.464265       0.888889  
15516                  0.087090       0.688464  
15501                  2.032897       0.535316  
15442                  0.561437       0.568871  
15456                  0.495675       0.478932  
15565                 14.333909       0.750000  
15440                  0.206438       0.521928  
15422                 26.508826       0.826087  
15475                  9.368487       0.446667  
15557  

Lo and behold, it appears that similar geographic areas that we discovered least contained the disease also exhibit some of the highest mortality rates by the last date of the data set provided.

One thing I notice right off the bat beyond geographic patterns is that amongst the countries with the highest mortality rates are both some of the richest and some of the poorest countries in the world. Comparing Covid outcome to other factors like GDP or legal regulations adopted during the pandemic would be very interesting, but for the scope of this quick exploration, we'll stick to the information that we already have for now to see what other patterns we might find.

In [143]:
# Reorganize the DataFrame by country, then by date (rather than by date, then by country):

unqiue_years = df["Date"].unique()
unqiue_countries = df["Country"].unique()

# Let's first separate the region of a country
population_per_country = df[["Country", "Population"]].drop_duplicates().set_index("Country")
population_per_country.sort_values('Population', inplace=True)

# Removing the region
# [["Date", "Country", "Case Rate", "Mortality Rate", "Mortality Rate / million"]]
data = df.drop(columns="Population").set_index(["Date", "Country"])

# Creating all possible "Year" "Country" combinations
data = data.reindex(pd.MultiIndex.from_product([unqiue_years, unqiue_countries]))

# Cleanup
data = data.reset_index().rename(columns={"level_0": "Date", "level_1": "Country"})

# Re-adding the region
data = data.merge(population_per_country, left_on="Country", right_index=True)

In [154]:
# Define function for even simpler interactive bar plotting:
def barplot(col, ymax):
  bar = px.bar(data,
              x='Country',
              y=col,
              color=col,
              animation_frame="Date",
              range_y=[0, ymax*1.1],
              range_color=[0, ymax],
              hover_data=[col, 'Population'],
              )
  bar.update_xaxes(
              categoryorder='array',
              categoryarray=population_per_country.index,
              )
  bar.update_layout(title_text=f'Covid-19 {col}',
                    # annotations=[dict(x=100, y=10.5, showarrow=False, text='May indicate if country size is indicative of pandemic handling?')],
                    title_x = 0.5,
                    xaxis_tickfont_size=10,
                    xaxis_tickangle=-45)
  bar.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 50
  bar.show()

In [155]:
col = 'Case Rate'
barplot(col, ymax=1)

col = 'Recovery Rate'
barplot(col, ymax=1)

col = 'Mortality Rate'
barplot(col, ymax=10)

Here we see an interesting trend: at first, larger countries exhibited better rates of recovery; but toward the end, we see that smaller countries generally yielded better rates of recovery than larger countries. Sadly, it's only a difference of roughly 0.25% in larger countries to 1% in smaller countries.

And, for now, here we have it. Covid mapped.

This project was really just designed to be a basic data exploration and sandbox for cool interactive plots.

For anyone interested in taking this to the next level, interesting next steps might include comparing Covid outcomes to indicators more useful than simply population, like:
*   Lockdown regulations (e.g. [here](https://www.kaggle.com/datasets/jcyzag/covid19-lockdown-dates-by-country))
*   Population density
*   GDP (e.g. [here](https://data.oecd.org/gdp/gross-domestic-product-gdp.htm))
*   Temperature (i.e., virus survival ability by climate)
*   Vaccine rollout (including timeline and brand)
